# BODS Data Extraction Test

## Library Imports

In [228]:
from BODSDataExtractor.extractor import TimetableExtractor
import pandas as pd
import numpy as np
import requests
from xml.etree import ElementTree as et
import xml.dom.minidom
import xmltodict
import json
from bs4 import BeautifulSoup as bsoup

# api key
api = 'a3eda657579ef98d499ef515fbb5a32a86b22248'
noc_70_74 = ['FBRI']
relevant_noc = ['FABD',
                'FYOR',
                'FWYO',
                'FBRA',
                'FLDS',
                'FHUD',
                'FHAL',
                'FSYO',
                'FMAN',
                'FLEI',
                'FSMR',
                'FECS',
                'FESX',
                'FDOR',
                'RRAR',
                'FTVA',
                'FHAM',
                'FHDO',
                'FBRI',
                'FCWL',
                'FBOS',
                'FPOT',
                'GLFI',
                'FSAV',
                'FRBE',
                'FNDE',
                'FDVN',
                'ABUS1',
                'FCYM',
                'FGLA',
                'FSCE']

## Timetable Data

Data sync daily from service provider.
Three main levels:

- Dataset level - Very high level info on datasets
    - One line = one dataset
    - One dataset contains multiple services
- Service / line level - Detailed info on each service
    - One line = one timetable xml file
    - Each service contains multiple timetables
- Stop level - A traditional timetable
    - One line = one bus stop

In [221]:
# Dataset level - Very high level info
dataset_level_object = TimetableExtractor(api_key=api # Your API Key Here
                                 ,limit=1 # How many datasets to view
                                 ,status = 'published' # Only view published datasets
                                 ,service_line_level=False # True if you require Service line data 
                                 ,stop_level=False # True if you require stop level data
                                 )

Fetching timetable metadata for up to 1 datasets...
Metadata downloaded for 1 datasets.
Merging OTC files...


In [3]:
dataset_level_object.metadata

id                                                url operator_name  \
0  464  https://data.bus-data.dft.gov.uk/timetable/dat...   Kinch Buses   

                                                name  \
0  Kinch Buses_Loughborough_Barrow-upon-Soar_2023...   

                                    description  \
0  Timetable data for Kinchbus (KBUS) services.   

                                             comment     status    nocs  \
0  sprint changing to Uni Out service from Sunday...  published  [KBUS]   

                    created                  modified  ...  \
0 2020-08-23 13:25:21+00:00 2024-05-20 15:15:14+00:00  ...   

                            lines          first_start_date  \
0  [11, 12, 2, 5, 9, CS, SKY, SP] 2023-09-24 00:00:00+00:00   

             first_end_date             last_end_date  \
0 2024-02-10 23:59:00+00:00 2024-06-22 23:59:00+00:00   

                                         admin_areas  \
0  [atco_code='109' name='Derby', atco_code='100'...   

                                          localities dq_score dq_rag  \
0  [gazetteer_id='E0036808' name='Alvaston', gaze...   100.0%  green   

  bods_compliance  filetype  
0            True       zip  

[1 rows x 21 columns]

In [222]:
# Service level - Very high level info
service_level_object = TimetableExtractor(api_key=api # Your API Key Here
                                 ,limit=1 # How many datasets to view
                                 ,status = 'published' # Only view published datasets
                                 ,service_line_level=True # True if you require Service line data 
                                 ,stop_level=False # True if you require stop level data
                                 )

Fetching timetable metadata for up to 1 datasets...
Metadata downloaded for 1 datasets.
Merging OTC files...
Fetching zip file from https://data.bus-data.dft.gov.uk/timetable/dataset/464/download/...
The following URLs failed: []


In [22]:
service_level_object.service_line_extract.head(3)

dq_score FileType OperatorName  ... LicenceNumber   ServiceCode expired service
0     100.0      zip  Kinch Buses  ...     PF0007157   PF0007157:1     No End Date
1     100.0      zip  Kinch Buses  ...     PF0007157  PF0007157:12     No End Date
2     100.0      zip  Kinch Buses  ...     PF0007157  PF0007157:12     No End Date

[3 rows x 27 columns]

In [227]:
# Stop level
stop_level_object = TimetableExtractor(api_key=api # Your API Key Here
                                 ,limit=100 # How many datasets to view
                                 ,status = 'published' # Only view published datasets
                                 ,service_line_level=True # True if you require Service line data 
                                 ,stop_level=False # True if you require stop level data
                                 )

Fetching timetable metadata for up to 100 datasets...
Metadata downloaded for 100 datasets.


SSLError: HTTPSConnectionPool(host='content.mgmt.dvsacloud.uk', port=443): Max retries exceeded with url: /olcs.prod.dvsa.aws/data-gov-uk-export/Bus_RegisteredOnly_C.csv (Caused by SSLError(SSLEOFError(8, '[SSL: UNEXPECTED_EOF_WHILE_READING] EOF occurred in violation of protocol (_ssl.c:1006)')))

In [219]:
check = stop_level_object.stop_level_extract.head(10)

NameError: name 'stop_level_object' is not defined

## API Access

The BODS data extractor only lets you get the metadata aka how the data look like.

Use the API to get the actual raw data

Buses: m1, m2, m3, 10, 46, U3, 70, 74, 19, 72 

https://data.bus-data.dft.gov.uk/guidance/requirements/?section=api

Let's take an example and walk through the query of m1's location

### m1 location

Step 1: Get the dataset ID

Get the NOC code [here](https://www.travelinedata.org.uk/traveline-open-data/transport-operations/about-2/) for First Bus, which is FBRI.


In [233]:
first_bus_services = TimetableExtractor(api_key=api # Your API Key Here
                                 ,limit=100 # commented out limit so will return all results within other parameters
                                 ,status = 'published' 
                                 ,service_line_level=True 
                                 ,stop_level=True 
                                #  ,nocs=['FBRI'] #values must be entered in this list format - each noc within quotes, separated by comma, all within []
                                #  ,search='First Bus' # this is actually redundant as nocs are specific to this operator, but included for demo purpose
                                 ,nocs=noc_70_74
                                 ,bods_compliant=True
                                 ,atco_code=['010'] # filter to stops within just bristol
                                 ,threaded=True
                                 )

Fetching timetable metadata for up to 100 datasets...
Metadata downloaded for 4 datasets.
Merging OTC files...
Fetching zip file from https://data.bus-data.dft.gov.uk/timetable/dataset/5815/download/...
Fetching zip file from https://data.bus-data.dft.gov.uk/timetable/dataset/5814/download/...
Fetching zip file from https://data.bus-data.dft.gov.uk/timetable/dataset/5813/download/...
Fetching zip file from https://data.bus-data.dft.gov.uk/timetable/dataset/2283/download/...
The following URLs failed: []
Generating Timetables...
Mapping service indexes...
Calculating vehicle journeys...
Timetables Generated!


In [244]:
first_bus_extracted = first_bus_services.stop_level_extract 
first_bus_extracted = first_bus_extracted[first_bus_extracted['LineName'].str.lower().isin(['70', '72','74','m1','m3','m4'])]
first_bus_extracted

FileName  \
41   70_74-FBRI070_FBRO074--FBRI-Bristol-2024-06-02...   
43   70_74-FBRI070_FBRO074--FBRI-Bristol-2024-06-02...   
45   72_72A-FBRI072_FBRI072A--FBRI-Bristol-2024-06-...   
106  70_74-FBRI070_FBRO074--FBRI-Bristol-2024-06-09...   
108  70_74-FBRI070_FBRO074--FBRI-Bristol-2024-06-09...   
110  72_72A-FBRI072_FBRI072A--FBRI-Bristol-2024-06-...   
283  M1-FBRIM01--FBRI-MST-2024-05-05-X06_-_MST_Lynx...   
287  M3_M3X_U3-FBRIM03_FBROM03X_BHAM0U3--FBRI-MST-2...   
291  m4-BHAM004--FBRI-MST-2024-05-05-X06_-_MST_Lynx...   
310  M1-FBRIM01--FBRI-MST-2024-06-02-X10_-_MST_Lynx...   
314  M3_M3X_U3-FBRIM03_FBROM03X_BHAM0U3--FBRI-MST-2...   
318  m4-BHAM004--FBRI-MST-2024-06-02-X10_-_MST_Lynx...   

                                                   URL  \
41   https://data.bus-data.dft.gov.uk/timetable/dat...   
43   https://data.bus-data.dft.gov.uk/timetable/dat...   
45   https://data.bus-data.dft.gov.uk/timetable/dat...   
106  https://data.bus-data.dft.gov.uk/timetable/dat...   
108  https://data.bus-data.dft.gov.uk/timetable/dat...   
110  https://data.bus-data.dft.gov.uk/timetable/dat...   
283  https://data.bus-data.dft.gov.uk/timetable/dat...   
287  https://data.bus-data.dft.gov.uk/timetable/dat...   
291  https://data.bus-data.dft.gov.uk/timetable/dat...   
310  https://data.bus-data.dft.gov.uk/timetable/dat...   
314  https://data.bus-data.dft.gov.uk/timetable/dat...   
318  https://data.bus-data.dft.gov.uk/timetable/dat...   

    OperatingPeriodStartDate RevisionNumber  OperatingDays  DatasetID  \
41                2024-06-02            225  Monday-Sunday       2283   
43                2024-06-02            225  Monday-Sunday       2283   
45                2024-06-02            225  Monday-Sunday       2283   
106               2024-06-09            227  Monday-Sunday       2283   
108               2024-06-09            227  Monday-Sunday       2283   
110               2024-06-09            227  Monday-Sunday       2283   
283               2024-05-05            678  Monday-Sunday       5814   
287               2024-05-05            678  Monday-Sunday       5814   
291               2024-05-05            678  Monday-Sunday       5814   
310               2024-06-02            694  Monday-Sunday       5814   
314               2024-06-02            694  Monday-Sunday       5814   
318               2024-06-02            694  Monday-Sunday       5814   

    LineName    ServiceCode  \
41        70  PH0000132:345   
43        74  PH0000132:345   
45        72  PH0000132:334   
106       74  PH0000132:345   
108       70  PH0000132:345   
110       72  PH0000132:334   
283       m1  PH0000132:417   
287       m3  PH0000132:362   
291       m4  PH0000132:419   
310       m1  PH0000132:417   
314       m3  PH0000132:362   
318       m4  PH0000132:419   

                           collated_timetable_outbound  \
41        Sequence Number Stop Point Ref Latitude L...   
43        Sequence Number Stop Point Ref Latitude L...   
45         Sequence Number Stop Point Ref Latitude ...   
106       Sequence Number Stop Point Ref Latitude L...   
108       Sequence Number Stop Point Ref Latitude L...   
110        Sequence Number Stop Point Ref Latitude ...   
283        Sequence Number Stop Point Ref Latitude ...   
287       Sequence Number Stop Point Ref Latitude L...   
291       Sequence Number Stop Point Ref Latitude L...   
310        Sequence Number Stop Point Ref Latitude ...   
314       Sequence Number Stop Point Ref Latitude L...   
318       Sequence Number Stop Point Ref Latitude L...   

                            collated_timetable_inbound  
41        Sequence Number Stop Point Ref Latitude L...  
43        Sequence Number Stop Point Ref Latitude L...  
45         Sequence Number Stop Point Ref Latitude ...  
106       Sequence Number Stop Point Ref Latitude L...  
108       Sequence Number Stop Point Ref Latitude L...  
110        Sequence Number Stop Point Ref Latitude ...  
283        Sequence Number S

Step 2: Query the data

In [51]:
response = requests.get("https://data.bus-data.dft.gov.uk/api/v1/datafeed/699/?api_key="+api)

In [54]:
response

<Response [200]>

In [134]:
disruption_data = requests.get("https://data.bus-data.dft.gov.uk/api/v1/siri-sx/?api_key="+api)
str(disruption_data.content)

'b\'<?xml version="1.0" encoding="UTF-8" standalone="yes"?>\\r\\n<Siri version="2.0" xmlns="http://www.siri.org.uk/siri" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.siri.org.uk/siri http://www.siri.org.uk/schema/2.0/xsd/siri.xsd">\\r\\n    <ServiceDelivery>\\r\\n        <ResponseTimestamp>2024-06-02T16:22:42.783Z</ResponseTimestamp>\\r\\n        <ProducerRef>DepartmentForTransport</ProducerRef>\\r\\n        <ResponseMessageIdentifier>46ed4750-6121-4d58-96f0-953b52b55a5c</ResponseMessageIdentifier>\\r\\n        <SituationExchangeDelivery>\\r\\n            <ResponseTimestamp>2024-06-02T16:22:42.783Z</ResponseTimestamp>\\r\\n            <Situations>\\r\\n                <PtSituationElement>\\r\\n                    <CreationTime>2024-06-01T14:47:42.154Z</CreationTime>\\r\\n                    <ParticipantRef>SYMCA</ParticipantRef>\\r\\n                    <SituationNumber>0133e39d-07cb-4a2e-aa22-83acf99307f0</SituationNumber>\\r\\n                 

In [133]:
data = json.dumps(xmltodict.parse(disruption_data), indent = 4)
print(data)

TypeError: a bytes-like object is required, not 'Response'

In [84]:
data = json.dumps(xmltodict.parse(disruption_data), indent = 4)
print(data)

TypeError: a bytes-like object is required, not 'Response'

Step 3: Interpret/Read the data

Using Beautiful Soup

In [123]:
bs_data = bsoup(response.content, 'xml')
# b_unique = bs_data.find('VehicleActivity', {'LineRef': '70'})
# b_unique

Using Element Tree

https://docs.python.org/3/library/xml.etree.elementtree.html#parsing-xml

https://www.datacamp.com/tutorial/python-xml-elementtree

LEARN XPATH!!!

In [103]:
response.content

b'<Siri xmlns="http://www.siri.org.uk/siri" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.siri.org.uk/siri http://www.siri.org.uk/schema/2.0/xsd/siri.xsd" version="2.0"><ServiceDelivery><ResponseTimestamp>2024-06-02T14:08:06.291960+00:00</ResponseTimestamp><ProducerRef>ItoWorld</ProducerRef><VehicleMonitoringDelivery><ResponseTimestamp>2024-06-02T14:08:06.291960+00:00</ResponseTimestamp><RequestMessageRef>40d71718-4b96-4a72-a760-7429f04dccc6</RequestMessageRef><ValidUntil>2024-06-02T14:13:06.291960+00:00</ValidUntil><ShortestPossibleCycle>PT5S</ShortestPossibleCycle><VehicleActivity><RecordedAtTime>2024-06-02T14:07:39+00:00</RecordedAtTime><ItemIdentifier>99d870c0-d56f-4c83-bd86-d14e7a8f3b43</ItemIdentifier><ValidUntilTime>2024-06-02T14:13:06.292143</ValidUntilTime><MonitoredVehicleJourney><LineRef>X4</LineRef><DirectionRef>inbound</DirectionRef><FramedVehicleJourneyRef><DataFrameRef>2024-06-02</DataFrameRef><DatedVehicleJourneyRef>1436</DatedVehi

In [170]:
tree = et.fromstring(response.content)
# Remove annoying namespaces
for elem in tree.iter():
    # print(elem.tag)
    if '}' in elem.tag:
        elem.tag = elem.tag.split('}', 1)[1]  # Strip namespace
    # Remove namespace from attributes
    attribs = elem.attrib
    # print(elem.attrib)
    for attrib in list(attribs.keys()):
        if '}' in attrib:
            new_attrib = attrib.split('}', 1)[1]
            attribs[new_attrib] = attribs.pop(attrib)
# et.tostring(tree)

In [173]:
# Find the <ServiceDelivery> element
service_delivery = tree.find('ServiceDelivery')
# Convert <ServiceDelivery> to an ElementTree object
service_delivery_tree = et.ElementTree(service_delivery)
for child in service_delivery:
    print(child.tag, child.attrib)

ResponseTimestamp {}
ProducerRef {}
VehicleMonitoringDelivery {}


In [183]:
print(et.tostring(service_delivery, encoding='utf8').decode('utf8'))

<?xml version='1.0' encoding='utf8'?>
<ServiceDelivery><ResponseTimestamp>2024-06-02T14:08:06.291960+00:00</ResponseTimestamp><ProducerRef>ItoWorld</ProducerRef><VehicleMonitoringDelivery><ResponseTimestamp>2024-06-02T14:08:06.291960+00:00</ResponseTimestamp><RequestMessageRef>40d71718-4b96-4a72-a760-7429f04dccc6</RequestMessageRef><ValidUntil>2024-06-02T14:13:06.291960+00:00</ValidUntil><ShortestPossibleCycle>PT5S</ShortestPossibleCycle><VehicleActivity><RecordedAtTime>2024-06-02T14:07:39+00:00</RecordedAtTime><ItemIdentifier>99d870c0-d56f-4c83-bd86-d14e7a8f3b43</ItemIdentifier><ValidUntilTime>2024-06-02T14:13:06.292143</ValidUntilTime><MonitoredVehicleJourney><LineRef>X4</LineRef><DirectionRef>inbound</DirectionRef><FramedVehicleJourneyRef><DataFrameRef>2024-06-02</DataFrameRef><DatedVehicleJourneyRef>1436</DatedVehicleJourneyRef></FramedVehicleJourneyRef><PublishedLineName>X4</PublishedLineName><OperatorRef>FBRI</OperatorRef><OriginRef>0190NSC30934</OriginRef><OriginName>Portishead_

In [200]:
for bus in service_delivery.findall("./VehicleMonitoringDelivery/VehicleActivity/MonitoredVehicleJourney/[LineRef='70']"):
    print(bus.attrib.get('DirectionRef'))

None
None
None
None
None
None
None
None


In [210]:
for bus in service_delivery.iterfind("./VehicleMonitoringDelivery/VehicleActivity/MonitoredVehicleJourney/[LineRef='70']"):
    line = et.ElementTree(bus)
    for child in line.iter():
        print(child.tag, child.text)

MonitoredVehicleJourney None
LineRef 70
DirectionRef outbound
FramedVehicleJourneyRef None
DataFrameRef 2024-06-01
DatedVehicleJourneyRef 1800
PublishedLineName 70
OperatorRef FBRI
OriginRef 0100FBX18342
OriginName Hengrove_Bus_Depot
DestinationRef 0170SGP90683
DestinationName UWE_Frenchay_Campus__B_
OriginAimedDepartureTime 2024-06-01T17:00:00+00:00
DestinationAimedArrivalTime 2024-06-01T18:10:00+00:00
VehicleLocation None
Longitude -2.545891
Latitude 51.499561
BlockRef 7002
VehicleRef FBRI-35110
MonitoredVehicleJourney None
LineRef 70
DirectionRef inbound
FramedVehicleJourneyRef None
DataFrameRef 2024-06-02
DatedVehicleJourneyRef 1426
PublishedLineName 70
OperatorRef FBRI
OriginRef 0170SGP90683
OriginName UWE_Frenchay_Campus__B_
DestinationRef 0100FBX18339
DestinationName Hengrove_Bus_Depot
OriginAimedDepartureTime 2024-06-02T13:25:00+00:00
DestinationAimedArrivalTime 2024-06-02T14:41:00+00:00
VehicleLocation None
Longitude -2.597241
Latitude 51.451871
Bearing 235.0
BlockRef 7001
Veh

### m1 timetable

In [217]:
timetable_data = requests.get("https://data.bus-data.dft.gov.uk/api/v1/dataset/2283/?api_key="+api)

json_data = json.loads(timetable_data.content)


In [218]:
json_data

{'id': 2283,
 'created': '2020-12-24T16:44:33+00:00',
 'modified': '2024-06-11T17:27:41+00:00',
 'operatorName': 'First Bus',
 'noc': ['FABD',
  'FYOR',
  'FWYO',
  'FBRA',
  'FLDS',
  'FHUD',
  'FHAL',
  'FSYO',
  'FMAN',
  'FLEI',
  'FSMR',
  'FECS',
  'FESX',
  'FDOR',
  'RRAR',
  'FTVA',
  'FHAM',
  'FHDO',
  'FBRI',
  'FCWL',
  'FBOS',
  'FPOT',
  'GLFI',
  'FSAV',
  'FRBE',
  'FNDE',
  'FDVN',
  'ABUS1',
  'FCYM',
  'FGLA',
  'FSCE'],
 'name': 'First Bus_Southmead_Kingswood_20240602_1',
 'description': 'FBRI-Bristol',
 'comment': 'Automatically detected change in data set',
 'status': 'published',
 'url': 'https://data.bus-data.dft.gov.uk/timetable/dataset/2283/download/',
 'extension': 'zip',
 'lines': ['1',
  '15',
  '2',
  '24',
  '2a',
  '3',
  '4',
  '41',
  '42',
  '43',
  '44',
  '45',
  '46',
  '47',
  '48',
  '48x',
  '49',
  '49x',
  '5',
  '6',
  '7',
  '70',
  '72',
  '73',
  '74',
  '75',
  '76',
  '77',
  '8',
  'A1',
  'AZ1',
  'AZ2',
  'NS',
  'SB1',
  'SB2',
  'S